In [1]:
import os, subprocess
from pathlib import Path, PurePosixPath
import gzip
import pandas as pd, numpy as np, pyranges as pr
import plotly.express as px

In [24]:
pd.set_option('display.max_columns', None)
pd.set_option('display.float_format', '{:.10f}'.format)

# UTR3

## Settings

[PyRanges v1.x GitHub](https://github.com/pyranges/pyranges_1.x)  
[PyRanges v1.x Docs](https://pyranges1.readthedocs.io/en/latest/index.html)

```{bash}
mamba env export -n utr3.venv > environment.yml
```

In [3]:
main_path = Path.cwd()

In [4]:
# Create tree
refs_dir = main_path / 'data/refs'
gnomad_dir = main_path / 'data/gnomad'

Path(refs_dir).mkdir(parents=True, exist_ok=True)
Path(gnomad_dir).mkdir(parents=True, exist_ok=True)

## Functions

In [139]:
def fetch_file(link, output_dir):
    command = f'wget --no-clobber -P {output_dir} {link}'
    subprocess.run(command, shell=True)
    filename = PurePosixPath(link).name
    return output_dir / filename


def define_join_type(row):
    feature_start = row['Start']
    feature_end = row['End']
    sv_start = row['Start_sv']
    sv_end = row['End_sv']

    join_type = np.nan
    if feature_start <= sv_start and feature_end >= sv_end: # SV полностью в feature
        join_type = 'sv_in_feature'
    elif sv_start <= feature_start and sv_end >= feature_end: # feature полностью в sv
        join_type = 'feature_in_sv'
    elif sv_start < feature_start and sv_end <= sv_end:
        join_type = 'sv_left_free'
    elif sv_start > feature_start and sv_end >= sv_end:
        join_type = 'sv_right_free'
    elif sv_start == feature_start and sv_end == sv_end:
        join_type = 'full_join'

    return join_type

## Fetch data

In [6]:
gff_filepath = fetch_file('https://ftp.ensembl.org/pub/release-115/gff3/homo_sapiens/Homo_sapiens.GRCh38.115.chr.gff3.gz', refs_dir)
gnomad_sv_filepath = fetch_file('https://storage.googleapis.com/gcp-public-data--gnomad/release/4.1/genome_sv/gnomad.v4.1.sv.sites.bed.gz', gnomad_dir)

File '/Users/andrejnekrasov/pro/my/utr3/data/refs/Homo_sapiens.GRCh38.115.chr.gff3.gz' already there; not retrieving.

File '/Users/andrejnekrasov/pro/my/utr3/data/gnomad/gnomad.v4.1.sv.sites.bed.gz' already there; not retrieving.



## Main

### Create PR/DF

In [7]:
gff_pr = pr.read_gff3(str(gff_filepath))

In [8]:
# Keep only the necessary columns (62 of 600...)
target_columns = ['#chrom', 'start', 'end', 'name', 'svtype', 'samples', 'MULTIALLELIC', 'ALGORITHMS', 'BOTHSIDES_SUPPORT', 'CHR2', 'CPX_INTERVALS', 'CPX_TYPE', 'END', 'END2', 'EVIDENCE', 'LOW_CONFIDENCE_REPETITIVE_LARGE_DUP', 'MEMBERS', 'NCR', 'OUTLIER_SAMPLE_ENRICHED_LENIENT', 'PAR', 'PCRMINUS_NCR', 'PCRPLUS_NCR', 'PESR_GT_OVERDISPERSION', 'POS2', 'PREDICTED_BREAKEND_EXONIC', 'PREDICTED_COPY_GAIN', 'PREDICTED_DUP_PARTIAL', 'PREDICTED_INTERGENIC', 'PREDICTED_INTRAGENIC_EXON_DUP', 'PREDICTED_INTRONIC', 'PREDICTED_INV_SPAN', 'PREDICTED_LOF', 'PREDICTED_MSV_EXON_OVERLAP', 'PREDICTED_NEAREST_TSS', 'PREDICTED_NONCODING_BREAKPOINT', 'PREDICTED_NONCODING_SPAN', 'PREDICTED_PARTIAL_DISPERSED_DUP', 'PREDICTED_PARTIAL_EXON_DUP', 'PREDICTED_PROMOTER', 'PREDICTED_TSS_DUP', 'PREDICTED_UTR', 'RESOLVED_POSTHOC', 'SOURCE', 'SVLEN', 'SVTYPE', 'UNRESOLVED_TYPE', 'AN', 'AC', 'AF', 'N_BI_GENOS', 'N_HOMREF', 'N_HET', 'N_HOMALT', 'FREQ_HOMREF', 'FREQ_HET', 'FREQ_HOMALT', 'CN_NUMBER', 'CN_COUNT', 'CN_STATUS', 'CN_FREQ', 'CN_NONREF_COUNT', 'CN_NONREF_FREQ']
target_columns[0:3] = ['Chromosome', 'Start', 'End']
sv_df = pd.read_csv(str(gnomad_sv_filepath), sep='\t', usecols=list(range(len(target_columns))), names=target_columns, comment='#')
sv_df['Chromosome'] = sv_df['Chromosome'].str.replace('chr', '')

sv_pr = pr.PyRanges(sv_df)

/var/folders/rf/k3pdmpqx0bjfvwyn2q6sw5v00000gn/T/ipykernel_16198/3892297514.py:4: DtypeWarning: Columns (10,11,24,25,26,28,29,30,31,32,33,36,37,38,39,40,42,57,58,59) have mixed types. Specify dtype option on import or set low_memory=False.
  sv_df = pd.read_csv(str(gnomad_sv_filepath), sep='\t', usecols=list(range(len(target_columns))), names=target_columns, comment='#')


### EDA (Exploratory Data Analysis)

In [9]:
gff_pr.Feature.value_counts()

Feature
exon                      3673949
CDS                       2284258
five_prime_UTR             426597
three_prime_UTR            340566
mRNA                       233574
lnc_RNA                    223403
biological_region          180392
ncRNA_gene                  41946
transcript                  28799
gene                        21547
pseudogenic_transcript      15201
pseudogene                  15198
snRNA                        1906
miRNA                        1879
unconfirmed_transcript       1108
snoRNA                        942
V_gene_segment                253
J_gene_segment                 97
scRNA                          49
rRNA                           49
D_gene_segment                 42
C_gene_segment                 29
chromosome                     25
tRNA                           22
processed_transcript           12
Name: count, dtype: int64

In [10]:
gff_pr.biotype.value_counts()

biotype
protein_coding                        231543
lncRNA                                224032
retained_intron                        34239
protein_coding_CDS_not_defined         26573
nonsense_mediated_decay                21949
processed_pseudogene                   18975
misc_RNA                                4414
unprocessed_pseudogene                  3898
snRNA                                   3802
miRNA                                   3758
transcribed_unprocessed_pseudogene      3176
transcribed_processed_pseudogene        2298
TEC                                     2127
snoRNA                                  1884
rRNA_pseudogene                          994
transcribed_unitary_pseudogene           402
IG_V_pseudogene                          374
IG_V_gene                                292
TR_V_gene                                214
unitary_pseudogene                       178
TR_J_gene                                158
non_stop_decay                           105
sc

In [11]:
sv_pr.svtype.value_counts()

svtype
DEL             1197080
BND              356035
DUP              269326
INS:ME:ALU       173374
INS               83441
INS:ME:LINE1      30223
INS:ME:SVA        17607
CPX               15189
DEL:ME:LINE1       8505
INV                2193
CNV                 721
DEL:ME:HERVK        693
CTX                  99
Name: count, dtype: int64

### Prepare GFF3 data

In [60]:
gff_pr['feature_len'] = (gff_pr['End'] - gff_pr['Start']).astype('int')

In [61]:
mrna_pr = gff_pr[gff_pr.Feature == 'mRNA']
three_utrs_pr = gff_pr[gff_pr.Feature == 'three_prime_UTR']

In [88]:
# Annotation of 3'-UTRs with mRNA (parent) data
target_columns = ['ID', 'Name', 'biotype', 'Parent', 'tag', 'transcript_support_level', 'feature_len'] # Replace the data in these empty 3'-UTRs columns with mRNA data
mrna_pr_short = mrna_pr[target_columns]
three_utrs_pr_annotated = three_utrs_pr.merge(mrna_pr_short, how='left', left_on='Parent', right_on='ID', suffixes=['_feature_suffix', ''])
three_utrs_pr_annotated[['Score', 'Frame']] = three_utrs_pr_annotated[['Score', 'Frame']].replace('.', np.nan)
three_utrs_pr_annotated = three_utrs_pr_annotated.dropna(axis=1, how='all') # Remove empty columns

# Stats
three_utrs_pr_annotated['biotype'].value_counts()


/var/folders/rf/k3pdmpqx0bjfvwyn2q6sw5v00000gn/T/ipykernel_16198/1958000034.py:5: FutureWarning:

Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`



biotype
protein_coding             202218
nonsense_mediated_decay    138264
protein_coding_LoF             50
Name: count, dtype: int64

In [89]:
# Keep only MANE_select / MANE_Select|Ensembl_canonical
three_utrs_pr_filtered = three_utrs_pr_annotated[three_utrs_pr_annotated['tag'].str.contains('MANE_Select', na=False, regex=True)]

# Stats
# MANE_select genes count = 19437 (release_1.5) from summary file: https://ftp.ncbi.nlm.nih.gov/refseq/MANE/MANE_human/release_1.5/
three_utrs_pr_filtered['biotype'].value_counts()

biotype
protein_coding    19757
Name: count, dtype: int64

In [90]:
pd.DataFrame(three_utrs_pr_filtered)

Chromosome          Source          Feature     Start       End Strand  \
0               1          havana  three_prime_UTR     70008     71585      +   
2               1          havana  three_prime_UTR    944153    944574      +   
13              1  ensembl_havana  three_prime_UTR    944202    944693      -   
75              1  ensembl_havana  three_prime_UTR    965191    965719      +   
87              1  ensembl_havana  three_prime_UTR    974575    975865      +   
...           ...             ...              ...       ...       ...    ...   
340532          Y          havana  three_prime_UTR  24905183  24907040      +   
340541          Y          havana  three_prime_UTR  25030900  25031222      -   
340542          Y          havana  three_prime_UTR  25031316  25031441      -   
340543          Y          havana  three_prime_UTR  25037991  25038097      -   
340544          Y  ensembl_havana  three_prime_UTR  25624527  25624902      +   

             Parent_feature_suffix  feature_len_feature_suffix  \
0       transcript:ENST00000641515                        1577   
2       transcript:ENST00000616016                         421   
13      transcript:ENST00000327044                         491   
75      transcript:ENST00000338591                         528   
87      transcript:ENST00000379410                        1290   
...                            ...                         ...   
340532  transcript:ENST00000682740                        1857   
340541  transcript:ENST00000382287                         322   
340542  transcript:ENST00000382287                         125   
340543  transcript:ENST00000382287                         106   
340544  transcript:ENST00000306609                         375   

                                ID         Name         biotype  \
0       transcript:ENST00000641515    OR4F5-201  protein_coding   
2       transcript:ENST00000616016   SAMD11-209  protein_coding   
13      transcript:ENST00000327044    NOC2L-201  protein_coding   
75      transcript:ENST00000338591   KLHL17-201  protein_coding   
87      transcript:ENST00000379410  PLEKHN1-203  protein_coding   
...                            ...          ...             ...   
340532  transcript:ENST00000682740     DAZ4-208  protein_coding   
340541  transcript:ENST00000382287    BPY2C-201  protein_coding   
340542  transcript:ENST00000382287    BPY2C-201  protein_coding   
340543  transcript:ENST00000382287    BPY2C-201  protein_coding   
340544  transcript:ENST00000306609     CDY1-201  protein_coding   

                      Parent  \
0       gene:ENSG00000186092   
2       gene:ENSG00000187634   
13      gene:ENSG00000188976   
75      gene:ENSG00000187961   
87      gene:ENSG00000187583   
...                      ...   
340532  gene:ENSG00000205916   
340541  gene:ENSG00000185894   
340542  gene:ENSG00000185894   
340543  gene:ENSG00000185894   
340544  gene:ENSG00000172288   

                                                      tag  \
0       gencode_basic,gencode_primary,Ensembl_canonica...   
2       gencode_basic,gencode_primary,Ensembl_canonica...   
13      gencode_basic,gencode_primary,Ensembl_canonica...   
75      gencode_basic,gencode_primary,Ensembl_canonica...   
87      gencode_basic,gencode_primary,Ensembl_canonica...   
...                                                   ...   
340532  gencode_basic,gencode_primary,Ensembl_canonica...   
340541  gencode_basic,gencode_primary,Ensembl_canonica...   
340542  gencode_basic,gencode_primary,Ensembl_canonica...   
340543  gencode_basic,gencode_primary,Ensembl_canonica...   
340544  gencode_basic,gencode_primary,Ensembl_canonica...   

                  transcript_support_level      feature_len  
0                                      NaN  6167.0000000000  
2       5 (assigned to previous version 4) 20652.0000000000  
13      1 (assigned to previous version 6) 15054.0000000000  
75      1 (assigned to previous version 7)  5136.0000000000  
87      

### Prepare SV data 

In [119]:
sv_del = sv_pr[sv_pr.svtype == "DEL"]
sv_del['sv_len'] = sv_del.End - sv_del.Start
sv_del['sv_id'] = sv_del['Chromosome'].astype('str') + ':' + sv_del['Start'].astype('str') + '-' + sv_del['End'].astype('str')

/var/folders/rf/k3pdmpqx0bjfvwyn2q6sw5v00000gn/T/ipykernel_16198/1883569321.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/rf/k3pdmpqx0bjfvwyn2q6sw5v00000gn/T/ipykernel_16198/1883569321.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [120]:
pd.DataFrame(sv_del)

Chromosome     Start       End                            name svtype  \
9                1     21999     30000  gnomAD-SV_v3_DEL_chr1_fa103016    DEL   
10               1     39999     47000  gnomAD-SV_v3_DEL_chr1_b26f63f7    DEL   
16               1     59100     59202  gnomAD-SV_v3_DEL_chr1_b0fb90d2    DEL   
18               1     62398     62489  gnomAD-SV_v3_DEL_chr1_7ef5c6e8    DEL   
22               1     66128     66613  gnomAD-SV_v3_DEL_chr1_ebfa4400    DEL   
...            ...       ...       ...                             ...    ...   
2154479          Y  56878224  56878748  gnomAD-SV_v3_DEL_chrY_a1db9958    DEL   
2154480          Y  56878242  56878635  gnomAD-SV_v3_DEL_chrY_193296dc    DEL   
2154481          Y  56878257  56878816  gnomAD-SV_v3_DEL_chrY_2d25b4a6    DEL   
2154482          Y  56878270  56878718  gnomAD-SV_v3_DEL_chrY_ab4f307f    DEL   
2154483          Y  56878973  56879563  gnomAD-SV_v3_DEL_chrY_0db85cf8    DEL   

         samples  MULTIALLELIC ALGORITHMS  BOTHSIDES_SUPPORT  CHR2  \
9            NaN         False      depth              False  chr1   
10           NaN         False      depth              False  chr1   
16           NaN         False      manta               True  chr1   
18           NaN         False      manta               True  chr1   
22           NaN         False      manta               True  chr1   
...          ...           ...        ...                ...   ...   
2154479      NaN         False       wham              False  chrY   
2154480      NaN         False       wham              False  chrY   
2154481      NaN         False       wham              False  chrY   
2154482      NaN         False       wham              False  chrY   
2154483      NaN         False       wham              False  chrY   

        CPX_INTERVALS CPX_TYPE       END  END2 EVIDENCE  \
9                 NaN      NaN     30000   NaN       RD   
10                NaN      NaN     47000   NaN       RD   
16                NaN      NaN     59202   NaN       SR   
18                NaN      NaN     62489   NaN       SR   
22                NaN      NaN     66613   NaN       SR   
...               ...      ...       ...   ...      ...   
2154479           NaN      NaN  56878748   NaN       SR   
2154480           NaN      NaN  56878635   NaN       SR   
2154481           NaN      NaN  56878816   NaN       SR   
2154482           NaN      NaN  56878718   NaN       PE   
2154483           NaN      NaN  56879563   NaN       SR   

         LOW_CONFIDENCE_REPETITIVE_LARGE_DUP MEMBERS          NCR  \
9                                      False     NaN 0.2886910141   
10                                     False     NaN 0.0000000000   
16                                     False     NaN 0.0004363670   
18                                     False     NaN 0.0007196230   
22                                     False     NaN 0.0172403008   
...                                      ...     ...          ...   
2154479                                False     NaN 0.5515679717   
2154480                                False     NaN 0.5075640082   
2154481                                False     NaN 0.5053740144   
2154482                                False     NaN 0.9981470108   
2154483                                False     NaN 0.5103430152   

         OUTLIER_SAMPLE_ENRICHED_LENIENT    PAR  PCRMINUS_NCR  PCRPLUS_NCR  \
9                                  False  False  0.2986469865 0.1756809950   
10                                 False  False  0.0000000000 0.0000000000   
16                                 False  False  0.0004498200 0.0002836610   
18                                 False  False  0.0006664000 0.0013237500   
22                                 False  False  0.0177679006 0.0112519003   
...                                  ...    ...           ...          ...   
2154479                            False  False           NaN 0.5222939849   
2154480                         

In [111]:
sv_del['AF'].describe(percentiles=[.1, .25, .5, .75, .9, .95, .99, .999])

count   1197080.0000000000
mean          0.0388642708
std           0.1348195999
min           0.0000080000
10%           0.0000080000
25%           0.0000160000
50%           0.0000500000
75%           0.0003650000
90%           0.0076041001
95%           0.5000000000
99%           0.5000000000
99.9%         0.9285709858
max           1.0000000000
Name: AF, dtype: float64

In [106]:
sv_del['sv_len'].describe(percentiles=[.1, .25, .5, .75, .9, .95, .99, .999])

count    1197080.0000000000
mean        5086.8619674541
std       154413.4211853280
min           51.0000000000
10%           99.0000000000
25%          324.0000000000
50%          609.0000000000
75%          964.0000000000
90%         5847.1000000001
95%        10927.0000000000
99%        82869.0499999998
99.9%     412913.1350000836
max     87762440.0000000000
Name: sv_len, dtype: float64

In [108]:
fig = px.histogram( 
    x=sv_del['sv_len'],
    nbins=300,
    log_y=True,
    title='gnomAD SV DEL lenght distribution (log)'
)
fig.show()

### Join GFF3 x gnomAD SV DEL

In [ ]:
# Join GFF x SV
three_utr_sv_joined_pr = three_utrs_pr_filtered.join_overlaps(sv_del, suffix='_sv', report_overlap_column='overlap_len')

In [141]:
# Define joint type
three_utr_sv_joined_pr['join_type'] = three_utr_sv_joined_pr.apply(define_join_type, axis=1)
three_utr_sv_joined_pr['join_type'].value_counts()

join_type
feature_in_sv    20428
sv_in_feature     8318
sv_right_free     3701
sv_left_free      3455
Name: count, dtype: int64

In [142]:
# Count joints by SV
joints_count_by_sv = three_utr_sv_joined_pr['sv_id'].value_counts().to_frame().reset_index()
joints_count_by_sv = joints_count_by_sv.rename(columns={'count': 'joins_count'})
joints_count_by_sv

sv_id  joins_count
0       2:49127869-136890309          447
1       5:85136274-161113193          436
2        X:35433370-85745406          314
3      7:101145532-150530080          301
4       1:58957768-111971259          270
...                      ...          ...
24904   17:21241460-21245422            1
24905   17:21239766-21240394            1
24906   17:21239063-21240340            1
24907   17:21187110-21193500            1
24908   19:39298451-39299199            1

[24909 rows x 2 columns]

In [143]:
# Add joints count data
three_utr_sv_joined_pr = three_utr_sv_joined_pr.merge(joints_count_by_sv, how='left')

In [144]:
pd.DataFrame(three_utr_sv_joined_pr).sort_values(by='sv_len')

Chromosome          Source          Feature      Start        End  \
16210         19  ensembl_havana  three_prime_UTR   16234435   16245906   
33313          9  ensembl_havana  three_prime_UTR   86287732   86288676   
29363          6          havana  three_prime_UTR  143940299  143941423   
16151         19          havana  three_prime_UTR   15088133   15092970   
20647         20          havana  three_prime_UTR     326872     330224   
...          ...             ...              ...        ...        ...   
19293          2  ensembl_havana  three_prime_UTR   98793845   98794531   
19294          2  ensembl_havana  three_prime_UTR   98997260   98998196   
19296          2          havana  three_prime_UTR   99150834   99151669   
19302          2  ensembl_havana  three_prime_UTR   99169262   99169374   
19793          2  ensembl_havana  three_prime_UTR  132147590  132148130   

      Strand       Parent_feature_suffix  feature_len_feature_suffix  \
16210      +  transcript:ENST00000291439                       11471   
33313      -  transcript:ENST00000375963                         944   
29363      -  transcript:ENST00000674357                        1124   
16151      +  transcript:ENST00000641398                        4837   
20647      +  transcript:ENST00000342665                        3352   
...      ...                         ...                         ...   
19293      -  transcript:ENST00000397899                         686   
19294      -  transcript:ENST00000393483                         936   
19296      +  transcript:ENST00000650052                         835   
19302      -  transcript:ENST00000289359                         112   
19793      -  transcript:ENST00000409867                         540   

                               ID           Name         biotype  \
16210  transcript:ENST00000291439      AP1M1-201  protein_coding   
33313  transcript:ENST00000375963       TUT7-206  protein_coding   
29363  transcript:ENST00000674357     PLAGL1-227  protein_coding   
16151  transcript:ENST00000641398      OR1I1-202  protein_coding   
20647  transcript:ENST00000342665      SOX12-201  protein_coding   
...                           ...            ...             ...   
19293  transcript:ENST00000397899     CRACDL-201  protein_coding   
19294  transcript:ENST00000393483     TSGA10-203  protein_coding   
19296  transcript:ENST00000650052    C2orf15-203  protein_coding   
19302  transcript:ENST00000289359      MITD1-201  protein_coding   
19793  transcript:ENST00000409867  ANKRD30BL-202  protein_coding   

                     Parent  \
16210  gene:ENSG00000072958   
33313  gene:ENSG00000083223   
29363  gene:ENSG00000118495   
16151  gene:ENSG00000094661   
20647  gene:ENSG00000177732   
...                     ...   
19293  gene:ENSG00000196872   
19294  gene:ENSG00000135951   
19296  gene:ENSG00000273045   
19302  gene:ENSG00000158411   
19793  gene:ENSG00000163046   

                                                     tag  \
16210  gencode_basic,gencode_primary,Ensembl_canonica...   
33313  gencode_basic,gencode_primary,Ensembl_canonica...   
29363  gencode_basic,gencode_primary,Ensembl_canonica...   
16151  gencode_basic,gencode_primary,Ensembl_canonica...   
20647  gencode_basic,gencode_primary,Ensembl_canonica...   
...                                                  ...   
19293  gencode_basic,gencode_primary,Ensembl_canonica...   
19294  gencode_basic,gencode_primary,Ensembl_canonica...   
19296  gencode_basic,gencode_primary,Ensembl_canonica...   
19302  gencode_basic,gencode_primary,Ensembl_canonica...   
19793  gencode_basic,gencode_primary,Ensembl_canonica...   

                  transcript_support_level       feature_len   Start_sv  \
16210   1 (assigned to previous version 7)  47996.0000000000   16235860   
33313   5 (assigned to previous version 7)  66678.0000000000   86288323   
29363                                  NaN  67960.0000000000  143940528   
16151                        

In [ ]:
# Filter joins by join type
targey_joint_types = ['sv_in_feature', 'sv_right_free', 'sv_left_free']
three_utr_sv_joined_pr_filtered = three_utr_sv_joined_pr.query('join_type in @targey_joint_types and ((Strand == "+" and join_type == "sv_right_free") or (Strand == "-" and join_type == "sv_left_free") or join_type == "sv_in_feature") and joins_count == 1')
three_utr_sv_joined_pr_filtered['join_type'].value_counts()

join_type
sv_in_feature    8124
sv_right_free    1924
sv_left_free     1589
Name: count, dtype: int64

In [154]:
three_utr_sv_joined_pr_filtered

index    |    Chromosome    Source          Feature          Start      ...
int64    |    object        object          object           int64      ...
-------  ---  ------------  --------------  ---------------  ---------  -----
71       |    1             ensembl_havana  three_prime_UTR  1233268    ...
105      |    1             ensembl_havana  three_prime_UTR  1385710    ...
106      |    1             ensembl_havana  three_prime_UTR  1385710    ...
108      |    1             ensembl_havana  three_prime_UTR  1427787    ...
...      |    ...           ...             ...              ...        ...
35627    |    X             ensembl_havana  three_prime_UTR  155054672  ...
35643    |    X             ensembl_havana  three_prime_UTR  155258234  ...
35658    |    X             havana          three_prime_UTR  155774738  ...
35659    |    X             havana          three_prime_UTR  155774738  ...
PyRanges with 11637 rows, 81 columns, and 1 index columns. (77 columns not shown: "End", "Strand", "Parent_feature_suffix", ...).
Contains 23 chromosomes and 2 strands.